# Instalando PyMove

In [42]:
# Necessário apenas no Colab
# %%capture
# !pip install pymove

# Breve Descrição do DataSet



Dados disponíveis no seguinte repositório da UCI: [GPS Trajectories Data Set](https://archive.ics.uci.edu/ml/datasets/GPS+Trajectories)

Os dados consiste em trajetórias reais coletadas dos usuários do aplicativo Go! Track(Ano de 2013). O GO! Track coleta continuamente pontos de GPS das trajetórias que as pessoas seguem enquanto estão no carro. O conjunto de dados usado contém 63 trajetórias com mais de 18.000 pontos.

**go_track_trackspoints.csv:** pontos de localização de cada trajetória.

- _id_: chave exclusiva para identificar cada ponto.
- _latitude_: latitude de onde o ponto está.
- _longitude_: longitude de onde o ponto está.
- _track_id_: identifique a trajetória à qual o ponto pertence.
- _time_: data e hora em que o ponto foi coletado (GMT-3).

# Leitura, Identificação e Conversão dos Dados

In [43]:
import pandas as pd
import pymove as pm

In [44]:
# Endereço no Colab
# filepath = '/content/drive/My Drive/Colab Notebooks/PyMove/Datas/GPS Trajectory/go_track_trackspoints.csv'

In [45]:
# Endereço Local
filepath = '../Datas/GPS Trajectory/go_track_trackspoints.csv'

In [46]:
df = pd.read_csv(filepath)

In [47]:
df.head()

id   latitude  longitude  track_id                 time
0   1 -10.939341 -37.062742         1  2014-09-13 07:24:32
1   2 -10.939341 -37.062742         1  2014-09-13 07:24:37
2   3 -10.939324 -37.062765         1  2014-09-13 07:24:42
3   4 -10.939211 -37.062843         1  2014-09-13 07:24:47
4   5 -10.938939 -37.062879         1  2014-09-13 07:24:53

In [48]:
df.drop(['id'], axis=1, inplace=True)

In [49]:
len(df.track_id.unique())

163

In [50]:
df.shape

(18107, 4)

In [51]:
df.head()

latitude  longitude  track_id                 time
0 -10.939341 -37.062742         1  2014-09-13 07:24:32
1 -10.939341 -37.062742         1  2014-09-13 07:24:37
2 -10.939324 -37.062765         1  2014-09-13 07:24:42
3 -10.939211 -37.062843         1  2014-09-13 07:24:47
4 -10.938939 -37.062879         1  2014-09-13 07:24:53

In [52]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18107 entries, 0 to 18106
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   latitude   18107 non-null  float64
 1   longitude  18107 non-null  float64
 2   track_id   18107 non-null  int64  
 3   time       18107 non-null  object 
dtypes: float64(2), int64(1), object(1)
memory usage: 566.0+ KB


In [53]:
df.time = pd.to_datetime(df.time)

In [54]:
df.head()

latitude  longitude  track_id                time
0 -10.939341 -37.062742         1 2014-09-13 07:24:32
1 -10.939341 -37.062742         1 2014-09-13 07:24:37
2 -10.939324 -37.062765         1 2014-09-13 07:24:42
3 -10.939211 -37.062843         1 2014-09-13 07:24:47
4 -10.938939 -37.062879         1 2014-09-13 07:24:53

In [55]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 18107 entries, 0 to 18106
Data columns (total 4 columns):
 #   Column     Non-Null Count  Dtype         
---  ------     --------------  -----         
 0   latitude   18107 non-null  float64       
 1   longitude  18107 non-null  float64       
 2   track_id   18107 non-null  int64         
 3   time       18107 non-null  datetime64[ns]
dtypes: datetime64[ns](1), float64(2), int64(1)
memory usage: 566.0 KB


In [56]:
dm = pm.PandasMoveDataFrame(
    df, latitude='latitude', 
    longitude='longitude', 
    datetime='time', 
    traj_id='track_id'
)

dm2 = pm.PandasMoveDataFrame(
    df, latitude='latitude', 
    longitude='longitude', 
    datetime='time', 
    traj_id='track_id'
)

In [57]:
dm.head()

lat        lon  id            datetime
0 -10.939342 -37.062740   1 2014-09-13 07:24:32
1 -10.939342 -37.062740   1 2014-09-13 07:24:37
2 -10.939324 -37.062763   1 2014-09-13 07:24:42
3 -10.939211 -37.062843   1 2014-09-13 07:24:47
4 -10.938939 -37.062878   1 2014-09-13 07:24:53

# Detecção de _Stop/Moves_ na Trajetória

A verificação de _stop/moves_ no PyMove pode ser identificada basicamente por duas maneiras. A primeira é diretamente por meio de uma visualização gráfica através da chamada da função _plot_stops_, descrita a seguir. As outras formas de identificação são por meio da chamada de funções que ao analizar o _dataset_, geram _features_ adicionais que armazenam informações referentes a um ponto de movimento ou um ponto de parada. Por "baixo dos panos", a função _plot_stops_ também faz algo semelhante para que possa mostrar um gráfico com esses pontos.

A seguir, temos essas duas maneiras básicas de identificação dos pontos de _stop/moves_ da trajetórias.

## Visualizando pontos de parada

A visualização dos pontos será feita por meio do módulo _visualization_ do PyMove.

In [58]:
import pymove.visualization as vsl

In [59]:
vsl.plot_stops(dm2)


Creating or updating distance features in meters...

...Sorting by id and datetime to increase performance

...Set id as index to increase attribution performance



Generating distance, time and speed features: 100%|██████████| 163/163 [00:00<00:00, 1164.40it/s]

...Reset index

..Total Time: 0.1969435214996338

Creating or updating features MOVE and STOPS...




....There are 2580 stops to this parameters



## Identificando _Stop/Moves_

A identificação dos _Stop/Moves_ será feita com base no que já existe implementado na biblioteca PyMove.

Antes de qualquer coisa, é possível perceber que o _dataset_ que usaremos contém apenas as features iniciais e que as modificações geradas pela função _plot_stops_ encontram-se em um outro _dataset_ que será descartado. Assim como as demais funções, armazenaremos os resultados do processamento de cada função em _datasets_ diferentes para que seus valores não se misturem.

In [60]:
dm.head()

lat        lon  id            datetime
0 -10.939342 -37.062740   1 2014-09-13 07:24:32
1 -10.939342 -37.062740   1 2014-09-13 07:24:37
2 -10.939324 -37.062763   1 2014-09-13 07:24:42
3 -10.939211 -37.062843   1 2014-09-13 07:24:47
4 -10.938939 -37.062878   1 2014-09-13 07:24:53

In [61]:
dm2.head()

id        lat        lon            datetime  dist_to_prev  dist_to_next  \
0   1 -10.939342 -37.062740 2014-09-13 07:24:32           NaN      0.000000   
1   1 -10.939342 -37.062740 2014-09-13 07:24:37      0.000000      2.934187   
2   1 -10.939324 -37.062763 2014-09-13 07:24:42      2.934187     15.475652   
3   1 -10.939211 -37.062843 2014-09-13 07:24:47     15.475652     30.418784   
4   1 -10.938939 -37.062878 2014-09-13 07:24:53     30.418784     44.240489   

   dist_prev_to_next situation  
0                NaN       nan  
1           2.934187      stop  
2          18.332698      move  
3          44.653001      move  
4          74.240342      move

In [62]:
dm2[dm2.situation=='stop'].shape

(2580, 8)

Após mostrar o cabeçalho do que já existe no _datsaet_, é possível perceber que foram adicionadas algumas colunas ao mesmo. Essas colunas são resultado da função de _plot_stops_ do módulo _visualization_.

No entanto, agora iremos observar os retornos do módulo _stay_point_detection_

### _stay_point_detection_

Usaremos as funções que já existem implementadas no módulo _stay_point_detection_. Para isso, importaremos o mesmo.

In [63]:
from pymove.preprocessing import stay_point_detection

#### _create_or_update_move_stop_by_dist_time_

Determina os pontos de _stop_ e _move_ do _dataframe_ baseado no tempo de leitura; se esses pontos já existirem, eles serão atualizados.

Essa função retorna o _dataframe_ com 2 features adicionais: _segment_stop_ e _stop_.
- _segment_stop_ indica o segmento de trajetória ao qual o ponto pertence.
- _stop_ indica se o ponto representa uma parada.


In [64]:
dmst = stay_point_detection.create_or_update_move_stop_by_dist_time(dm, inplace=False)

Split trajectories by max distance between adjacent points: 30

Creating or updating distance features in meters...

...Sorting by id and datetime to increase performance

...Set id as index to increase attribution performance



Generating distance, time and speed features: 100%|██████████| 163/163 [00:00<00:00, 743.88it/s] 

...Reset index

..Total Time: 0.2582120895385742
...setting id as index



Generating segment_stop:  17%|█▋        | 27/163 [00:00<00:00, 267.05it/s]

id: 14 has not point to split
id: 71 has not point to split
id: 148 has not point to split


...

id: 38030 has not point to split
... Reseting index
...No trajs with only one point. (18107, 8)

Creating or updating distance features in meters...

...Sorting by id and datetime to increase performance

...Set id as index to increase attribution performance




Generating distance, time and speed features: 100%|██████████| 163/163 [00:00<00:00, 871.27it/s] 

...Reset index

..Total Time: 0.22201824188232422
------------------------------------------


Creating or updating distance, time and speed features in meters by seconds

...Sorting by segment_stop and datetime to increase performance

...Set segment_stop as index to a higher peformance




Generating distance features:  42%|████▏     | 3800/8964 [00:01<00:02, 2440.98it/s]/home/user/anaconda3/envs/pymove/lib/python3.7/site-packages/pymove-1.1.4+3.gc05ce58-py3.7.egg/pymove/core/dataframe.py:1097: RuntimeWarning: invalid value encountered in true_divide
  data_.at[idx, DIST_TO_PREV] / time_prev
Generating distance features: 100%|██████████| 8964/8964 [00:05<00:00, 1601.92it/s]


...Reset index...

..Total Time: 6.438
Create or update stop as True or False
...Creating stop features as True or False using 900 to time in seconds
False    16798
True      1309
Name: stop, dtype: int64

Total Time: 17.66 seconds
-----------------------------------------------------



In [65]:
dmst.head()

segment_stop  id        lat        lon            datetime  dist_to_prev  \
0             1   1 -10.939342 -37.062740 2014-09-13 07:24:32           NaN   
1             1   1 -10.939342 -37.062740 2014-09-13 07:24:37      0.000000   
2             1   1 -10.939324 -37.062763 2014-09-13 07:24:42      2.934187   
3             1   1 -10.939211 -37.062843 2014-09-13 07:24:47     15.475652   
4             2   1 -10.938939 -37.062878 2014-09-13 07:24:53           NaN   

   dist_to_next  dist_prev_to_next  time_to_prev  speed_to_prev   stop  
0      0.000000                NaN           NaN            NaN  False  
1      2.934187           2.934187           5.0       0.000000  False  
2     15.475652          18.332698           5.0       0.586837  False  
3     30.418784          44.653001           5.0       3.095130  False  
4     44.240489          74.240342           NaN            NaN  False

In [66]:
dmst[dmst.stop].head()

segment_stop  id        lat        lon            datetime  \
2248           963  26 -10.924294 -37.104790 2014-10-22 10:24:27   
2249           963  26 -10.924559 -37.104748 2014-10-22 10:24:37   
2250           963  26 -10.924553 -37.104740 2014-10-22 10:24:48   
2251           963  26 -10.924553 -37.104740 2014-10-22 10:24:58   
2252           963  26 -10.924520 -37.104755 2014-10-22 10:25:09   

      dist_to_prev  dist_to_next  dist_prev_to_next  time_to_prev  \
2248           NaN     29.920119          81.682837           NaN   
2249     29.920119      0.998859          29.397265          10.0   
2250      0.998859      0.000000           0.998859          11.0   
2251      0.000000      4.145351           4.145351          10.0   
2252      4.145351     12.908755           9.031110          11.0   

      speed_to_prev  stop  
2248            NaN  True  
2249       2.992012  True  
2250       0.090805  True  
2251       0.000000  True  
2252       0.376850  True

In [67]:
dmst[dmst.stop].shape

(1309, 11)

In [68]:
pm.visualization.plot_markers(dmst[dmst.stop])

#### _create_update_move_and_stop_by_radius_

Localiza os pontos de _stop_ e _move_ do _dataframe_ baseado no raio; se esses pontos já existirem, eles serão atualizados.

Essa função retorna o _dataframe_ com 2 features adicionais: _segment_stop_ e _new_label_.
- _segment_stop_ indica o segmento de trajetória ao qual o ponto pertence.
- _new_label_ indica se o ponto representa um ponto de parada ou um ponto móvel.

Essa função é usada "por baixo dos panos" pela função _plot_stops_ do módulo _visualization_. Dessa maneira, os dados gerados por ela são similares aos gerados pela função de visualização.

In [69]:
dmsr = stay_point_detection.create_update_move_and_stop_by_radius(dm,inplace=False)


Creating or updating features MOVE and STOPS...


Creating or updating distance features in meters...

...Sorting by id and datetime to increase performance

...Set id as index to increase attribution performance



Generating distance, time and speed features: 100%|██████████| 163/163 [00:06<00:00, 26.41it/s]


...Reset index

..Total Time: 16.816667318344116

....There are 2580 stops to this parameters



In [70]:
dmsr.head()

id        lat        lon            datetime  dist_to_prev  dist_to_next  \
0   1 -10.939342 -37.062740 2014-09-13 07:24:32           NaN      0.000000   
1   1 -10.939342 -37.062740 2014-09-13 07:24:37      0.000000      2.934187   
2   1 -10.939324 -37.062763 2014-09-13 07:24:42      2.934187     15.475652   
3   1 -10.939211 -37.062843 2014-09-13 07:24:47     15.475652     30.418784   
4   1 -10.938939 -37.062878 2014-09-13 07:24:53     30.418784     44.240489   

   dist_prev_to_next situation  
0                NaN       nan  
1           2.934187      stop  
2          18.332698      move  
3          44.653001      move  
4          74.240342      move

In [71]:
dmsr[dmsr.situation=='stop'].shape

(2580, 8)

In [72]:
vsl.plot_markers(dmsr[dmsr.situation=='stop'])

### _compression_

Usaremos as funções que existem implementadas no módulo _compression_. Para isso, importaremos o mesmo.

In [73]:
from pymove.preprocessing import compression

#### _compress_segment_stop_to_point_

Comprime as trajetórias usando os pontos de permanência do _dataframe_. Comprima um segmento para definir o ponto _lat_mean_ e _lon_mean_ para cada segmento.

Retorna o _dataframe_ com 2 features adicionais: _segment_stop_, _stop_, _lat_mean_ e _lon_mean_.
- _segment_stop_ indica o segmento de trajetória ao qual o ponto pertence.
- _stop_ indica se o ponto representa uma parada.
- _lat_mean_ e _lon_mean_:
 - se a opção padrão for usada, _lat_mean_ e _lon_mean_ serão definidos com base no ponto que se repete mais dentro o segmento.
 - Por outro lado, se a opção centróide for usada, _lat_mean_ e _lon_mean_ serão definidas pelo centróide do todos os pontos no segmento.

In [74]:
dmcp = compression.compress_segment_stop_to_point(dm)

Split trajectories by max distance between adjacent points: 30

Creating or updating distance features in meters...

...Sorting by id and datetime to increase performance

...Set id as index to increase attribution performance



Generating distance, time and speed features: 100%|██████████| 163/163 [00:00<00:00, 516.10it/s]

...Reset index

..Total Time: 8.928182125091553
...setting id as index



Generating segment_stop:   0%|          | 0/163 [00:00<?, ?it/s]

id: 14 has not point to split


...

...Reset index

..Total Time: 0.5200514793395996
------------------------------------------


Creating or updating distance, time and speed features in meters by seconds

...Sorting by segment_stop and datetime to increase performance

...Set segment_stop as index to a higher peformance




Generating distance features:  42%|████▏     | 3747/8964 [00:01<00:01, 3031.47it/s]/home/user/anaconda3/envs/pymove/lib/python3.7/site-packages/pymove-1.1.4+3.gc05ce58-py3.7.egg/pymove/core/dataframe.py:1097: RuntimeWarning: invalid value encountered in true_divide
  data_.at[idx, DIST_TO_PREV] / time_prev
Generating distance features: 100%|██████████| 8964/8964 [00:03<00:00, 2860.44it/s]


...Reset index...

..Total Time: 3.172
Create or update stop as True or False
...Creating stop features as True or False using 900 to time in seconds
False    16798
True      1309
Name: stop, dtype: int64

Total Time: 14.74 seconds
-----------------------------------------------------

...setting mean to lat and lon...
...get only segments stop...


Generating segment_stop and stop: 100%|██████████| 8/8 [00:00<00:00, 12.42it/s]

...Dropping 1293 points...
...Shape_before: 18107
...Current shape: 16814
-----------------------------------------------------



In [75]:
dmcp.head()

segment_stop  id        lat        lon            datetime  dist_to_prev  \
0             1   1 -10.939342 -37.062740 2014-09-13 07:24:32           NaN   
1             1   1 -10.939342 -37.062740 2014-09-13 07:24:37      0.000000   
2             1   1 -10.939324 -37.062763 2014-09-13 07:24:42      2.934187   
3             1   1 -10.939211 -37.062843 2014-09-13 07:24:47     15.475652   
4             2   1 -10.938939 -37.062878 2014-09-13 07:24:53           NaN   

   dist_to_next  dist_prev_to_next  time_to_prev  speed_to_prev   stop  \
0      0.000000                NaN           NaN            NaN  False   
1      2.934187           2.934187           5.0       0.000000  False   
2     15.475652          18.332698           5.0       0.586837  False   
3     30.418784          44.653001           5.0       3.095130  False   
4     44.240489          74.240342           NaN            NaN  False   

   lat_mean  lon_mean  
0       NaN       NaN  
1       NaN       NaN  
2       NaN       NaN  
3       NaN       NaN  
4       NaN       NaN

In [76]:
dmcp[dmcp.stop].shape

(16, 13)

In [77]:
dmcp[dmcp.stop]

segment_stop     id        lat        lon            datetime  \
2248            963     26 -10.924294 -37.104790 2014-10-22 10:24:27   
2318            963     26 -10.926540 -37.101929 2014-10-22 10:45:35   
2649           1045     27 -10.924294 -37.104790 2014-10-22 10:24:27   
2719           1045     27 -10.926540 -37.101929 2014-10-22 10:45:35   
8357           4291    134 -10.896932 -37.079685 2015-02-14 10:28:37   
8660           4291    134 -10.897087 -37.079720 2015-02-14 10:55:29   
8661           4292    135 -10.896932 -37.079685 2015-02-14 10:28:37   
8964           4292    135 -10.897087 -37.079720 2015-02-14 10:55:29   
10117          5018    147 -10.922647 -37.047188 2015-02-23 05:54:44   
10322          5018    147 -10.922628 -37.047073 2015-02-23 06:12:56   
13200          6491  37967 -10.896848 -37.053547 2015-05-20 18:41:30   
13295          6491  37967 -10.896863 -37.053543 2015-05-20 18:59:41   
16225          7963  38019 -10.944241 -37.069176 2015-06-09 04:20:46   
16375          7963  38019 -10.944236 -37.068634 2015-06-09 04:37:23   
16813          8189  38031 -10.922748 -37.047306 2015-07-23 09:03:11   
16918          8189  38031 -10.922745 -37.047363 2015-07-23 09:27:51   

       dist_to_prev  dist_to_next  dist_prev_to_next  time_to_prev  \
2248            NaN     29.920119          81.682837           NaN   
2318       3.078025     36.841701          34.087703          10.0   
2649            NaN     29.920119          81.682837           NaN   
2719       3.078025     36.841701          34.087703          10.0   
8357            NaN      7.360138                NaN           NaN   
8660       0.000000           NaN                NaN           5.0   
8661            NaN      7.360138                NaN           NaN   
8964       0.000000           NaN                NaN           5.0   
10117           NaN     14.168456          40.897641           NaN   
10322      4.325883           NaN                NaN           5.0   
13200           NaN      0.532216                NaN           NaN   
13295      0.000000           NaN                NaN          12.0   
16225           NaN     22.698523          76.842330           NaN   
16375      0.000000           NaN                NaN           9.0   
16813           NaN     12.392177                NaN           NaN   
16918      0.000000           NaN                NaN          15.0   

       speed_to_prev  stop   lat_mean   lon_mean  
2248             NaN  True -10.924553 -37.104740  
2318        0.307802  True -10.924553 -37.104740  
2649             NaN  True -10.924553 -37.104740  
2719        0.307802  True -10.924553 -37.104740  
8357             NaN  True -10.897094 -37.079708  
8660        0.000000  True -10.897094 -37.079708  
8661             NaN  True -10.897094 -37.079708  
8964        0.000000  True -10.897094 -37.079708  
10117            NaN  True -10.922691 -37.047279  
10322       0.865177  True -10.922691 -37.047279  
13200            NaN  True -10.896859 -37.053547  
13295       0.000000  True -10.896859 -37.053547  
16225            NaN  True -10.944238 -37.068638  
16375       0.000000  True -10.944238 -37.068638  
16813            NaN  True -10.922760 -37.047329  
16918       0.000000  True -10.922760 -37.047329

In [ ]:
vsl.plot_markers(dmcp[dmcp.stop])

#### _compress_segment_stop_to_point_optimizer_

Comprime as trajetórias usando os pontos de parada do _dataframe_. Comprime um segmento para definir a configuração _lat_mean_ e _lon_mean_ para cada segmento.

Retorna o _dataframe_ com 2 features adicionais: _segment_stop_, _stop_, _lat_mean_ e _lon_mean_.
- _segment_stop_ indica o segmento de trajetória ao qual o ponto pertence.
- _lat_mean_ e _lon_mean_:
 - se a opção padrão for usada, _lat_mean_ e _lon_mean_ serão definidos com base no ponto que se repete mais dentro o segmento.
 - Por outro lado, se a opção centróide for usada, _lat_mean_ e _lon_mean_ serão definidas pelo centróide do todos os pontos no segmento

In [ ]:
dmco = compression.compress_segment_stop_to_point_optimizer(dm)

In [ ]:
dmco.head()

In [ ]:
dmco[dmco.stop].shape

In [ ]:
vsl.plot_markers(dmco[dmco.stop])

E essa seria apenas uma simples visualização de algumas funções que já presentes no PyMove que faz essa detecção dos pontos de _stop/moves_ na trajetória.